In [24]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse
import os

%run ../moreprocessing.py

In [17]:
# Merge excel files from GEO

df1 = pd.DataFrame(pd.read_excel("GSE139358_RNA-Seq_gene_rpkm_33_samples.xlsx", header=0, skiprows=4))
df1 = df1.drop("Type", axis=1)
df1 = df1.rename({"Genes":"ProbeID"}, axis=1)

df2 = pd.DataFrame(pd.read_excel("GSE139358_RNA-Seq_gene_rpkm_18_samples.xlsx", header=0, skiprows=5))
df2 = df2.rename({"ID":"ProbeID"}, axis=1)

expr = df2.merge(df1, on="ProbeID", how="outer")
expr.insert(1, "Name", expr["ProbeID"])
expr

ProbeID       Name  NDN_01_LE  NDN_02_LE  NDN_03_LE  NDN_04_PPAR  \
0           A1BG       A1BG   0.357715   0.364738   0.072958     0.254913   
1       A1BG-AS1   A1BG-AS1   0.265644   0.297931   0.064137     0.266780   
2           A1CF       A1CF   0.009266   0.007980   0.006782     0.009252   
3            A2M        A2M   0.017316   0.019878   0.006350     0.017188   
4        A2M-AS1    A2M-AS1   0.000000   0.010961   0.000000     0.000000   
...          ...        ...        ...        ...        ...          ...   
26202    SKIV2L2    SKIV2L2        NaN        NaN        NaN          NaN   
26203   C9orf142   C9orf142        NaN        NaN        NaN          NaN   
26204     ATP5G1     ATP5G1        NaN        NaN        NaN          NaN   
26205      CECR5      CECR5        NaN        NaN        NaN          NaN   
26206  LINC00998  LINC00998        NaN        NaN        NaN          NaN   

       NDN_05_PPAR   NDN_06_PPAR  LDG_01_LE_CD10_pos  LDG_02_LE_CD10_pos  ...  \
0         0.109645  1.006620e-01            1.313700            0.512977  ...   
1         0.061887  2.525460e-01            0.497438            0.590311  ...   
2         0.017361  2.670460e-02            0.014462            0.025928  ...   
3         0.006362  3.643620e-27            0.083309            0.105522  ...   
4         0.000000  1.104160e-02            0.179455            0.375973  ...   
...            ...           ...                 ...                 ...  ...   
26202          NaN           NaN                 NaN                 NaN  ...   
26203          NaN           NaN                 NaN                 NaN  ...   
26204          NaN           NaN                 NaN                 NaN  ...   
26205          NaN           NaN                 NaN                 NaN  ...   
26206          NaN           NaN                 NaN                 NaN  ...   

       LDG_SLE_02_imm  LDG_SLE_03_mat  LDG_SLE_04_mat  LDG_SLE_05_mat  \
0                 NaN             NaN             NaN             NaN   
1                 NaN             NaN             NaN             NaN   
2                 NaN             NaN             NaN             NaN   
3                 NaN             NaN             NaN             NaN   
4                 NaN             NaN             NaN             NaN   
...               ...             ...             ...             ...   
26202        0.535015         1.06695        0.361320         1.04868   
26203        7.912340         5.88890        3.458540        14.72050   
26204        0.758616         3.10486        0.000000         5.08495   
26205        1.179890         2.61202        0.503328         2.16110   
26206        0.480614         2.14793        0.088382         2.07097   

       LDG_SLE_06_imm  LDG_SLE_07_imm  LDG_SLE_08_mat  LDG_SLE_09_mat  \
0                 NaN             NaN             NaN             NaN   
1                 NaN             NaN             NaN             NaN   
2                 NaN             NaN             NaN             NaN   
3                 NaN             NaN             NaN             NaN   
4                 NaN             NaN             NaN             NaN   
...               ...             ...             ...             ...   
26202        0.567239        1.188210        0.533611        1.721730   
26203        7.401040        1.947130        6.773260        9.229820   
26204        1.502330        0.757622        0.514460        1.308150   
26205        1.312690        0.352214        1.259540        0.859915   
26206        0.615101        0.434271        0.147445        1.108450   

       LDG_SLE_10_mat  LDG_SLE_11_mat  
0                 NaN             NaN  
1                 NaN             NaN  
2                 NaN             NaN  
3                 NaN             NaN  
4                 NaN             NaN  
...               ...             ...  
26202        0.938688        0.718455  
26203        1.200970        5.259630

In [18]:
# Normalize and log transform

genes = expr.loc[:,["ProbeID", "Name"]]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID       Name  NDN_01_LE  NDN_02_LE  NDN_03_LE  NDN_04_PPAR  \
0           A1BG       A1BG   0.441181   0.448624   0.101594     0.327587   
1       A1BG-AS1   A1BG-AS1   0.339872   0.376214   0.089683     0.341166   
2           A1CF       A1CF   0.013307   0.011467   0.009752     0.013286   
3            A2M        A2M   0.024768   0.028396   0.009131     0.024586   
4        A2M-AS1    A2M-AS1   0.000000   0.015727   0.000000     0.000000   
...          ...        ...        ...        ...        ...          ...   
26202    SKIV2L2    SKIV2L2        NaN        NaN        NaN          NaN   
26203   C9orf142   C9orf142        NaN        NaN        NaN          NaN   
26204     ATP5G1     ATP5G1        NaN        NaN        NaN          NaN   
26205      CECR5      CECR5        NaN        NaN        NaN          NaN   
26206  LINC00998  LINC00998        NaN        NaN        NaN          NaN   

       NDN_05_PPAR   NDN_06_PPAR  LDG_01_LE_CD10_pos  LDG_02_LE_CD10_pos  ...  \
0         0.150098  1.383715e-01            1.210202            0.597390  ...   
1         0.086630  3.248636e-01            0.582496            0.669309  ...   
2         0.024832  3.802115e-02            0.020714            0.036929  ...   
3         0.009149  5.256632e-27            0.115445            0.144728  ...   
4         0.000000  1.584236e-02            0.238120            0.460452  ...   
...            ...           ...                 ...                 ...  ...   
26202          NaN           NaN                 NaN                 NaN  ...   
26203          NaN           NaN                 NaN                 NaN  ...   
26204          NaN           NaN                 NaN                 NaN  ...   
26205          NaN           NaN                 NaN                 NaN  ...   
26206          NaN           NaN                 NaN                 NaN  ...   

       LDG_SLE_02_imm  LDG_SLE_03_mat  LDG_SLE_04_mat  LDG_SLE_05_mat  \
0                 NaN             NaN             NaN             NaN   
1                 NaN             NaN             NaN             NaN   
2                 NaN             NaN             NaN             NaN   
3                 NaN             NaN             NaN             NaN   
4                 NaN             NaN             NaN             NaN   
...               ...             ...             ...             ...   
26202        0.618253        1.047503        0.445006        1.034695   
26203        3.155804        2.784274        2.156571        3.974575   
26204        0.814441        2.037333        0.000000        2.605245   
26205        1.124255        1.852806        0.588160        1.660427   
26206        0.566196        1.654403        0.122184        1.618695   

       LDG_SLE_06_imm  LDG_SLE_07_imm  LDG_SLE_08_mat  LDG_SLE_09_mat  \
0                 NaN             NaN             NaN             NaN   
1                 NaN             NaN             NaN             NaN   
2                 NaN             NaN             NaN             NaN   
3                 NaN             NaN             NaN             NaN   
4                 NaN             NaN             NaN             NaN   
...               ...             ...             ...             ...   
26202        0.648225        1.129751        0.616933        1.444524   
26203        3.070568        1.559311        2.958520        3.354709   
26204        1.323272        0.813625        0.598804        1.206737   
26205        1.209572        0.435324        1.176029        0.895237   
26206        0.691624        0.520318        0.198425        1.076183   

       LDG_SLE_10_mat  LDG_SLE_11_mat  
0                 NaN             NaN  
1                 NaN             NaN  
2                 NaN             NaN  
3                 NaN             NaN  
4                 NaN             NaN  
...               ...             ...  
26202        0.955081        0.781112  
26203        1.138140        2.646077

In [19]:
# Replace headers with GSM IDs

ih = pd.DataFrame(pd.read_csv("GSE139358-GPL21290-ih.txt", sep="\t", header=0))
gsm_dict = {ih["ClinicalHeader"][i].split(" ")[0]:ih["ArrayID"][i] for i in range(len(ih.index))}
expr = expr.rename(gsm_dict, axis=1)
expr

ProbeID       Name  GSM4138717  GSM4138718  GSM4138719  GSM4138720  \
0           A1BG       A1BG    0.441181    0.448624    0.101594    0.327587   
1       A1BG-AS1   A1BG-AS1    0.339872    0.376214    0.089683    0.341166   
2           A1CF       A1CF    0.013307    0.011467    0.009752    0.013286   
3            A2M        A2M    0.024768    0.028396    0.009131    0.024586   
4        A2M-AS1    A2M-AS1    0.000000    0.015727    0.000000    0.000000   
...          ...        ...         ...         ...         ...         ...   
26202    SKIV2L2    SKIV2L2         NaN         NaN         NaN         NaN   
26203   C9orf142   C9orf142         NaN         NaN         NaN         NaN   
26204     ATP5G1     ATP5G1         NaN         NaN         NaN         NaN   
26205      CECR5      CECR5         NaN         NaN         NaN         NaN   
26206  LINC00998  LINC00998         NaN         NaN         NaN         NaN   

       GSM4138721    GSM4138722  GSM4138723  GSM4138724  ...  GSM4138707  \
0        0.150098  1.383715e-01    1.210202    0.597390  ...         NaN   
1        0.086630  3.248636e-01    0.582496    0.669309  ...         NaN   
2        0.024832  3.802115e-02    0.020714    0.036929  ...         NaN   
3        0.009149  5.256632e-27    0.115445    0.144728  ...         NaN   
4        0.000000  1.584236e-02    0.238120    0.460452  ...         NaN   
...           ...           ...         ...         ...  ...         ...   
26202         NaN           NaN         NaN         NaN  ...    0.618253   
26203         NaN           NaN         NaN         NaN  ...    3.155804   
26204         NaN           NaN         NaN         NaN  ...    0.814441   
26205         NaN           NaN         NaN         NaN  ...    1.124255   
26206         NaN           NaN         NaN         NaN  ...    0.566196   

       GSM4138708  GSM4138709  GSM4138710  GSM4138711  GSM4138712  GSM4138713  \
0             NaN         NaN         NaN         NaN         NaN         NaN   
1             NaN         NaN         NaN         NaN         NaN         NaN   
2             NaN         NaN         NaN         NaN         NaN         NaN   
3             NaN         NaN         NaN         NaN         NaN         NaN   
4             NaN         NaN         NaN         NaN         NaN         NaN   
...           ...         ...         ...         ...         ...         ...   
26202    1.047503    0.445006    1.034695    0.648225    1.129751    0.616933   
26203    2.784274    2.156571    3.974575    3.070568    1.559311    2.958520   
26204    2.037333    0.000000    2.605245    1.323272    0.813625    0.598804   
26205    1.852806    0.588160    1.660427    1.209572    0.435324    1.176029   
26206    1.654403    0.122184    1.618695    0.691624    0.520318    0.198425   

       GSM4138714  GSM4138715  GSM4138716  
0             NaN         NaN         NaN  
1             NaN         NaN         NaN  
2             NaN         NaN         NaN  
3             NaN         NaN         NaN  
4             NaN         NaN         NaN  
...           ...         ...         ...  
26202    1.444524    0.955081    0.781112  
26203    3.354709    1.138140    2.646077  
26204    1.206737    0.563375    0.076376  
26205    0.895237    0.219281    0.606987  
26206    1.076183    0.542393    0.169479  

[26207 rows x 53 columns]

In [25]:
writeExprIdx(expr)

14-Jul-2022 17:00:26 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358 already exists. Skipping.
14-Jul-2022 17:00:26 INFO GEOparse - File already exist: using local version.
14-Jul-2022 17:00:26 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358_family.soft.gz: 
14-Jul-2022 17:00:26 DEBUG GEOparse - DATABASE: GeoMiame
14-Jul-2022 17:00:26 DEBUG GEOparse - SERIES: GSE139358
14-Jul-2022 17:00:26 DEBUG GEOparse - PLATFORM: GPL21290
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138684
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138685
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138686
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138687
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138688
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138689
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138690
14-Jul-2022 17:00:26 DEBUG GEOparse - SAMPLE: GSM4138691
14-Jul-2022 17:00:26 DEBU

Writing to current directory
Starting expr at /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358-GPL21290-expr.txt
Done writing expr
Writing idx to /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358-GPL21290-idx.txt
Starting make_idx
Done with make_idx


In [27]:
expr.loc[expr["ProbeID"] == "CCDC88A"]

ProbeID     Name  GSM4138717  GSM4138718  GSM4138719  GSM4138720  \
2866  CCDC88A  CCDC88A    0.259283    0.219548    0.148334    0.126696   

      GSM4138721  GSM4138722  GSM4138723  GSM4138724  ...  GSM4138707  \
2866    0.148601    0.198454    2.948126    2.884561  ...         NaN   

      GSM4138708  GSM4138709  GSM4138710  GSM4138711  GSM4138712  GSM4138713  \
2866         NaN         NaN         NaN         NaN         NaN         NaN   

      GSM4138714  GSM4138715  GSM4138716  
2866         NaN         NaN         NaN  

[1 rows x 53 columns]

In [53]:
%run runmoreprocessing.py

Database ID NEU10
Dataset Name Mistry 2019 Neutrophils
key macv:neu:
Configuration file (default /Users/rohan) 


08-Jul-2022 11:50:38 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358 already exists. Skipping.
08-Jul-2022 11:50:38 INFO GEOparse - File already exist: using local version.
08-Jul-2022 11:50:38 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358_family.soft.gz: 
08-Jul-2022 11:50:38 DEBUG GEOparse - DATABASE: GeoMiame
08-Jul-2022 11:50:38 DEBUG GEOparse - SERIES: GSE139358
08-Jul-2022 11:50:38 DEBUG GEOparse - PLATFORM: GPL21290
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138684
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138685
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138686
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138687
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138688
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138689
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138690
08-Jul-2022 11:50:38 DEBUG GEOparse - SAMPLE: GSM4138691
08-Jul-2022 11:50:38 DEBU

[NEU10]
name = Mistry 2019 Neutrophils
expr = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358-GPL21290-expr.txt
index = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358-GPL21290-idx.txt
survival = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358-GPL21290-survival.txt
indexHeader = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358-GPL21290-ih.txt
info = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358-GPL21290-info.txt
key = macv:neu:
source = GSE139358
Write to file? y/n y


08-Jul-2022 11:50:44 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358 already exists. Skipping.
08-Jul-2022 11:50:44 INFO GEOparse - File already exist: using local version.
08-Jul-2022 11:50:44 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE139358/GSE139358_family.soft.gz: 
08-Jul-2022 11:50:44 DEBUG GEOparse - DATABASE: GeoMiame
08-Jul-2022 11:50:44 DEBUG GEOparse - SERIES: GSE139358
08-Jul-2022 11:50:44 DEBUG GEOparse - PLATFORM: GPL21290
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138684
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138685
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138686
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138687
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138688
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138689
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138690
08-Jul-2022 11:50:44 DEBUG GEOparse - SAMPLE: GSM4138691
08-Jul-2022 11:50:44 DEBU